In [1]:
import datetime as dt

import pandas as pd
import pandas_market_calendars as mcal
import polars as pl

nse = mcal.get_calendar("NSE")

df = pd.read_csv("Combined Rolling Pivots BNF NF MIDCP 3 4 4.csv")

In [2]:
df.tail(30)

Unnamed: 0 Trade Type        Signal Generated At  \
4133        3538       LONG  2024-06-03 14:15:00+05:30   
4134        1777       LONG  2024-06-03 14:15:00+05:30   
4135        3539      SHORT  2024-06-04 09:15:00+05:30   
4136        4157      SHORT  2024-06-04 09:15:00+05:30   
4137        1778      SHORT  2024-06-04 09:15:00+05:30   
4138        4158       LONG  2024-06-05 10:15:00+05:30   
4139        3540       LONG  2024-06-05 10:15:00+05:30   
4140        1779       LONG  2024-06-05 11:15:00+05:30   
4141        1780      SHORT  2024-06-06 11:15:00+05:30   
4142        3541      SHORT  2024-06-06 11:15:00+05:30   
4143        1781       LONG  2024-06-06 15:15:00+05:30   
4144        3542       LONG  2024-06-06 15:15:00+05:30   
4145        4160      SHORT  2024-06-07 12:15:00+05:30   
4146        4159       LONG  2024-06-07 12:15:00+05:30   
4147        4161       LONG  2024-06-07 14:15:00+05:30   
4148        1782       LONG  2024-06-07 15:15:00+05:30   
4149        1783      SHORT  2024-06-07 15:15:00+05:30   
4150        3543      SHORT  2024-06-07 15:15:00+05:30   
4151        3545      SHORT  2024-06-10 10:15:00+05:30   
4152        3546       LONG  2024-06-10 10:15:00+05:30   
4153        1784       LONG  2024-06-10 10:15:00+05:30   
4154        3544       LONG  2024-06-10 10:15:00+05:30   
4155        4162       LONG  2024-06-10 11:15:00+05:30   
4156        3547      SHORT  2024-06-10 14:15:00+05:30   
4157        1785      SHORT  2024-06-10 14:15:00+05:30   
4158        1786       LONG  2024-06-11 12:15:00+05:30   
4159        3548      SHORT  2024-06-11 14:15:00+05:30   
4160        1787      SHORT  2024-06-11 14:15:00+05:30   
4161        3549       LONG  2024-06-12 09:15:00+05:30   
4162        1788       LONG  2024-06-12 09:15:00+05:30   

                     Entry Time  Entry Price  Initial SL  \
4133  2024-06-03 15:15:00+05:30     23267.05    23161.00   
4134  2024-06-03 15:15:00+05:30     50965.60    50611.40   
4135  2024-06-04 10:15:00+05:30     22389.85    23308.25   
4136  2024-06-04 10:15:00+05:30     11233.30    11766.55   
4137  2024-06-04 10:15:00+05:30     48741.55    51133.20   
4138  2024-06-05 11:15:00+05:30     11247.85    10755.70   
4139  2024-06-05 11:15:00+05:30     22355.40    21791.95   
4140  2024-06-05 12:15:00+05:30     48000.60    46446.80   
4141  2024-06-06 12:15:00+05:30     49160.80    49672.75   
4142  2024-06-06 12:15:00+05:30     22675.80    22910.15   
4143  2024-06-07 09:15:00+05:30     49367.10    48948.30   
4144  2024-06-07 09:15:00+05:30     22865.45    22669.50   
4145  2024-06-07 13:15:00+05:30     11694.20    11736.45   
4146  2024-06-07 13:15:00+05:30     11694.20    11736.45   
4147  2024-06-07 15:15:00+05:30     11761.75    11690.15   
4148  2024-06-10 09:15:00+05:30     49752.35    49909.20   
4149  2024-06-10 09:15:00+05:30     49752.35    49909.20   
4150  2024-06-10 09:15:00+05:30     23262.80    23320.20   
4151  2024-06-10 11:15:00+05:30     23303.00    23411.90   
4152  2024-06-10 11:15:00+05:30     23362.85    23233.05   
4153  2024-06-10 11:15:00+05:30     49986.40    49654.20   
4154  2024-06-10 11:15:00+05:30     23303.00    23411.90   
4155  2024-06-10 12:15:00+05:30     11671.35    11583.45   
4156  2024-06-10 15:15:00+05:30     23228.45    23377.35   
4157  2024-06-10 15:15:00+05:30     49716.80    50099.20   
4158  2024-06-11 13:15:00+05:30     49905.00    49750.20   
4159  2024-06-11 15:15:00+05:30     23260.35    23389.45   
4160  2024-06-11 15:15:00+05:30     49682.40    49970.30   
4161  2024-06-12 10:15:00+05:30     23420.35    23232.00   
4162  2024-06-12 10:15:00+05:30     50222.00    49615.55   

                      Exit Time  Exit Price                 Remarks  \
4133  2024-06-04 09:15:00+05:30    23153.60  Gap Outside Initial SL   
4134  2024-06-04 09:15:00+05:30    50505.55  Gap Outside Initial SL   
4135  2024-06-05 11:15:00+05:30    22355.40                Reversed   
4136  2024-06-05 11:15:00+05:30    11247.85                Rev

In [3]:
import sys

sys.path.append("..")
from tooling.enums import AssetClass, Index, Spot, StrikeSpread
from tooling.fetch import fetch_option_data, fetch_spot_data
from tooling.filter import find_atm, option_tool

pd.set_option("display.max_rows", 25_000)
pd.set_option("display.max_columns", 500)
pl.Config.set_tbl_cols(500)
pl.Config.set_tbl_rows(10_000)

pd.options.display.float_format = '{:.4f}'.format

In [4]:
def get_expiry(f_today):

    if (f_today <= dt.date(2024, 1, 25)) and (f_today >= dt.date(2024, 1, 18)):
        f_expiry = dt.date(2024, 1, 25)
    elif (f_today <= dt.date(2024, 1, 31)) and (f_today >= dt.date(2024, 1, 26)):
        f_expiry = dt.date(2024, 1, 31)
    elif (f_today <= dt.date(2024, 2, 22)) and (f_today >= dt.date(2024, 2, 29)):
        f_expiry = dt.date(2024, 2, 29)
    elif (f_today <= dt.date(2024, 3, 25)) and (f_today >= dt.date(2024, 3, 27)):
        f_expiry = dt.date(2024, 2, 27)
    elif f_today < dt.date(2023, 9, 1):
        days_to_thursday = (3 - f_today.weekday()) % 7
        nearest_thursday = f_today + dt.timedelta(days=days_to_thursday)
        f_expiry = nearest_thursday
        if nse.valid_days(start_date=nearest_thursday, end_date=nearest_thursday).empty:
            f_expiry = nearest_thursday - dt.timedelta(days=1)
    elif f_today >= dt.date(2023, 9, 1):
        if f_today.day < 24:
            days_to_wednesday = (2 - f_today.weekday()) % 7
            nearest_wednesday = f_today + dt.timedelta(days=days_to_wednesday)
            f_expiry = nearest_wednesday
            if nse.valid_days(
                start_date=nearest_wednesday, end_date=nearest_wednesday
            ).empty:
                f_expiry = nearest_wednesday - dt.timedelta(days=1)
        else:
            days_to_thursday = (3 - f_today.weekday()) % 7
            nearest_thursday = f_today + dt.timedelta(days=days_to_thursday)
            f_expiry = nearest_thursday
            if nse.valid_days(
                start_date=nearest_thursday, end_date=nearest_thursday
            ).empty:
                f_expiry = nearest_thursday - dt.timedelta(days=1)
    return f_expiry


def get_expiry_nifty(f_today):

    days_to_thursday = (3 - f_today.weekday()) % 7
    nearest_thursday = f_today + dt.timedelta(days=days_to_thursday)
    f_expiry = nearest_thursday
    if nse.valid_days(start_date=nearest_thursday, end_date=nearest_thursday).empty:
        f_expiry = nearest_thursday - dt.timedelta(days=1)
    return f_expiry


def get_expiry_midcp(f_today):

    days_to_monday = (0 - f_today.weekday()) % 7
    nearest_monday = f_today + dt.timedelta(days=days_to_monday)
    f_expiry = nearest_monday
    if nse.valid_days(start_date=nearest_monday, end_date=nearest_monday).empty:
        f_expiry = nearest_monday - dt.timedelta(days=3)
    return f_expiry


def get_option_contract_name(symbol, strike, expiry, opt_type):
    temp = "0"
    mth = expiry.month

    if (expiry + dt.timedelta(days=7)).month != expiry.month:
        date_string = expiry.strftime("%y%b").upper()
        return f"{symbol}{date_string}{strike}{opt_type}"
    else:
        if expiry.day <= 9:
            date_string = f"{expiry.year - 2000}{mth}{temp}{expiry.day}"
        else:
            date_string = f"{expiry.year - 2000}{mth}{expiry.day}"
        return f"{symbol}{date_string}{strike}{opt_type}"

In [8]:
def round_to_nearest_100(value):
    return 100 * round(value / 100)


def round_to_nearest_50(value):
    return 50 * round(value / 50)


def round_to_nearest_25(value):
    return 25 * round(value / 25)


df["Entry Time"] = pd.to_datetime(df["Entry Time"])
df["Exit Time"] = pd.to_datetime(df["Exit Time"])

df["Strike"] = df.apply(
    lambda row: (
        round_to_nearest_25(row["Entry Price"])
        if row["Index"] == "MIDCPNIFTY"
        else (
            round_to_nearest_50(row["Entry Price"])
            if row["Index"] == "NIFTY"
            else round_to_nearest_100(row["Entry Price"])
        )
    ),
    axis=1,
)

df["Option Type"] = df.apply(
    lambda row: ("PE" if row["Trade Type"] == "LONG" else "CE"), axis=1
)
# df["Expiry"] = df.apply(
#     lambda row: (
#         get_expiry_midcp(row["Exit Time"].date())
#         if row["Index"] == "MIDCPNIFTY"
#         else (
#             get_expiry_nifty(row["Exit Time"].date())
#             if row["Index"] == "NIFTY"
#             else get_expiry(row["Exit Time"].date())
#         )
#     ),
#     axis=1,
# )
df["Expiry"] = df.apply(
    lambda row: (
        get_expiry_midcp(row["Entry Time"].date() + dt.timedelta(days=7))
        if row["Index"] == "MIDCPNIFTY"
        else (
            get_expiry_nifty(row["Entry Time"].date() + dt.timedelta(days=7))
            if row["Index"] == "NIFTY"
            else get_expiry(row["Entry Time"].date() + dt.timedelta(days=7))
        )
    ),
    axis=1,
)
df["Option Contract"] = df.apply(
    lambda row: get_option_contract_name(
        row["Index"], row["Strike"], row["Expiry"], row["Option Type"]
    ),
    axis=1,
)
df["Instrument"] = df.apply(
    lambda row: (
        "midcpnifty"
        if row["Index"] == "MIDCPNIFTY"
        else ("nifty" if row["Index"] == "NIFTY" else "bnf")
    ),
    axis=1,
)

for i in range(0, len(df)):
    print(df.iloc[i]['Entry Time'].date())
    opt_df = await fetch_option_data(
        index=df.iloc[i]["Instrument"],
        expiry=df.iloc[i]["Expiry"],
        strike=df.iloc[i]["Strike"],
        asset_class=df.iloc[i]["Option Type"][-2:-1],
        start_date=df.iloc[i]["Entry Time"].date(),
        start_time=df.iloc[i]["Entry Time"].time(),
        end_date=df.iloc[i]["Exit Time"].date(),
        end_time=df.iloc[i]["Exit Time"].time(),
    )
    # print(opt_df)
    if not isinstance(opt_df, str):
        opt_df = opt_df.to_pandas()
        entry_price = opt_df.iloc[0]["c"]
        exit_price = opt_df.iloc[-1]["c"]
        print('Sold At  ', entry_price, ' Bought Back At ', exit_price)
    else:
        print(opt_df)
        entry_price = float('nan')
        exit_price = float('nan')

    df.at[i, "Option Entry Price"] = entry_price
    df.at[i, "Option Exit Price"] = exit_price

# df.tail(30)

2018-01-01
No data found for nifty index option 10500CE & expiry 2018-01-11.
2018-01-02
Sold At   160.0  Bought Back At  113.25
2018-01-04
Sold At   137.0  Bought Back At  77.7
2018-01-05
Sold At   148.0  Bought Back At  146.0
2018-01-05
No data found for nifty index option 10550CE & expiry 2018-01-11.
2018-01-05
Sold At   162.3  Bought Back At  66.0
2018-01-05
No data found for nifty index option 10550PE & expiry 2018-01-11.
2018-01-08
Sold At   126.0  Bought Back At  97.05
2018-01-08
No data found for nifty index option 10600CE & expiry 2018-01-11.
2018-01-09
No data found for nifty index option 10600CE & expiry 2018-01-11.
2018-01-09
Sold At   77.25  Bought Back At  77.25
2018-01-09
No data found for nifty index option 10650CE & expiry 2018-01-11.
2018-01-09
No data found for nifty index option 10650PE & expiry 2018-01-11.
2018-01-09
Sold At   106.5  Bought Back At  116.95
2018-01-09
No data found for nifty index option 10650PE & expiry 2018-01-11.
2018-01-09
Sold At   106.5  Bought

In [17]:
df

Unnamed: 0 Trade Type        Signal Generated At  \
0           1789      SHORT  2018-01-01 11:15:00+05:30   
1              0      SHORT  2018-01-01 15:15:00+05:30   
2              1       LONG  2018-01-04 11:15:00+05:30   
3              2      SHORT  2018-01-05 10:15:00+05:30   
4           1790      SHORT  2018-01-05 10:15:00+05:30   
5              3       LONG  2018-01-05 12:15:00+05:30   
6           1791       LONG  2018-01-05 12:15:00+05:30   
7              4      SHORT  2018-01-08 10:15:00+05:30   
8           1792      SHORT  2018-01-08 12:15:00+05:30   
9           1793      SHORT  2018-01-08 15:15:00+05:30   
10             6      SHORT  2018-01-09 10:15:00+05:30   
11          1795      SHORT  2018-01-09 10:15:00+05:30   
12          1796       LONG  2018-01-09 10:15:00+05:30   
13             7       LONG  2018-01-09 10:15:00+05:30   
14          1794       LONG  2018-01-09 10:15:00+05:30   
15             5       LONG  2018-01-09 10:15:00+05:30   
16             9      SHORT  2018-01-09 12:15:00+05:30   
17          1797      SHORT  2018-01-09 12:15:00+05:30   
18             8       LONG  2018-01-09 12:15:00+05:30   
19            10      SHORT  2018-01-09 14:15:00+05:30   
20          1798      SHORT  2018-01-10 10:15:00+05:30   
21          1799       LONG  2018-01-10 12:15:00+05:30   
22            11       LONG  2018-01-10 12:15:00+05:30   
23            13      SHORT  2018-01-11 13:15:00+05:30   
24          1800      SHORT  2018-01-11 13:15:00+05:30   
25            12       LONG  2018-01-11 13:15:00+05:30   
26            14      SHORT  2018-01-12 10:15:00+05:30   
27          1801      SHORT  2018-01-12 10:15:00+05:30   
28          1802       LONG  2018-01-12 13:15:00+05:30   
29            15       LONG  2018-01-12 13:15:00+05:30   
30            16      SHORT  2018-01-15 15:15:00+05:30   
31            17       LONG  2018-01-16 11:15:00+05:30   
32          1803      SHORT  2018-01-16 13:15:00+05:30   
33          1804      SHORT  2018-01-16 15:15:00+05:30   
34            18       LONG  2018-01-17 12:15:00+05:30   
35            19      SHORT  2018-01-18 10:15:00+05:30   
36          1805       LONG  2018-01-18 10:15:00+05:30   
37          1806      SHORT  2018-01-18 12:15:00+05:30   
38          1807       LONG  2018-01-19 11:15:00+05:30   
39            20       LONG  2018-01-19 13:15:00+05:30   
40          1808      SHORT  2018-01-19 13:15:00+05:30   
41          1809       LONG  2018-01-22 10:15:00+05:30   
42            21      SHORT  2018-01-25 10:15:00+05:30   
43            22      SHORT  2018-01-29 14:15:00+05:30   
44            23       LONG  2018-01-30 15:15:00+05:30   
45          1810      SHORT  2018-01-31 10:15:00+05:30   
46            24      SHORT  2018-01-31 15:15:00+05:30   
47          1811      SHORT  2018-02-01 10:15:00+05:30   
48            25       LONG  2018-02-01 10:15:00+05:30   
49            26      SHORT  2018-02-01 14:15:00+05:30   
50            27       LONG  2018-02-02 11:15:00+05:30   
51          1812       LONG  2018-02-02 11:15:00+05:30   
52            28      SHORT  2018-02-02 13:15:00+05:30   
53          1813      SHORT  2018-02-02 13:15:00+05:30   
54            29       LONG  2018-02-05 10:15:00+05:30   
55          1814       LONG  2018-02-05 10:15:00+05:30   
56          1815       LONG  2018-02-06 10:15:00+05:30   
57            30       LONG  2018-02-06 11:15:00+05:30   
58            31      SHORT  2018-02-07 10:15:00+05:30   
59          1816      SHORT  2018-02-07 10:15:00+05:30   
60            32       LONG  2018-02-08 09:15:00+05:30   
61          1817       LONG  2018-02-08 09:15:00+05:30   
62            33      SHORT  2018-02-08 11:15:00+05:30   
63          1818       LONG  2018-02-09 12:15:00+05:30   
64            34      SHORT  2018-02-09 13:15:00+05:30   
65          1819      SHORT  2018-02-12 15:15:00+05:30   
66            35      SHORT  2018-02-12 15:15:00+05:30   
67            36      SHORT  2018-02-14 10:15:00+05:30   
68  

In [16]:
df['Option Points'] = df['Option Entry Price'] - df['Option Exit Price']
df['Option Points w CS'] = (df['Option Entry Price'] - df['Option Exit Price']) - (0.01 * (df['Option Entry Price'] + df['Option Exit Price']))
df['Options PnL'] = df['Option Points'] * df['Qty']
df['Options PnL w CS'] = df['Option Points w CS'] * df['Qty']
df['Options ROI%'] = df['Options PnL'] * 100 / 1000000
df['Options ROI% w CS'] = df['Options PnL w CS'] * 100 / 1000000

In [18]:
df['Options ROI% w CS'].sum()

1859.2718294282943

In [19]:
stats_df8 = pd.DataFrame(
    index=range(2018, 2025),
    columns=[
        "Total ROI",
        "Total Trades",
        "Win Rate",
        "Avg Profit% per Trade",
        "Avg Loss% per Trade",
        "Max Drawdown",
        "ROI/DD Ratio",
    ],
)
combined_df_sorted = df
# Iterate over each year
for year in range(2018, 2025):
    # Filter trades for the current year
    year_trades = combined_df_sorted[(combined_df_sorted["Trade Year"] == year)]

    # Calculate total ROI
    total_roi = year_trades["Options ROI% w CS"].sum()

    # Calculate total number of trades
    total_trades = len(year_trades)

    # Calculate win rate
    win_rate = (year_trades["Options ROI% w CS"] > 0).mean() * 100

    # Calculate average profit per trade
    avg_profit = year_trades[year_trades["Options ROI% w CS"] > 0]["Options ROI% w CS"].mean()

    # Calculate average loss per trade
    avg_loss = year_trades[year_trades["Options ROI% w CS"] < 0]["Options ROI% w CS"].mean()

    # Calculate maximum drawdown
    max_drawdown = (
        year_trades["Options ROI% w CS"].cumsum() - year_trades["Options ROI% w CS"].cumsum().cummax()
    ).min()

    # Calculate ROI/DD ratio
    roi_dd_ratio = total_roi / abs(max_drawdown)

    # Store the statistics in the DataFrame
    stats_df8.loc[year] = [
        total_roi,
        total_trades,
        win_rate,
        avg_profit,
        avg_loss,
        max_drawdown,
        roi_dd_ratio,
    ]

# Calculate overall statistics
overall_total_roi = stats_df8["Total ROI"].sum()
overall_total_trades = stats_df8["Total Trades"].sum()
overall_win_rate = (combined_df_sorted["Options ROI% w CS"] > 0).mean() * 100
overall_avg_profit = combined_df_sorted[combined_df_sorted["Options ROI% w CS"] > 0][
    "Options ROI% w CS"
].mean()
overall_avg_loss = combined_df_sorted[combined_df_sorted["Options ROI% w CS"] < 0][
    "Options ROI% w CS"
].mean()
overall_max_drawdown = (
    combined_df_sorted["Options ROI% w CS"].cumsum()
    - combined_df_sorted["Options ROI% w CS"].cumsum().cummax()
).min()
overall_roi_dd_ratio = overall_total_roi / abs(overall_max_drawdown)

# Store the overall statistics in the DataFrame
stats_df8.loc["Overall"] = [
    overall_total_roi,
    overall_total_trades,
    overall_win_rate,
    overall_avg_profit,
    overall_avg_loss,
    overall_max_drawdown,
    overall_roi_dd_ratio,
]
stats_df8

Total ROI Total Trades Win Rate Avg Profit% per Trade  \
2018     128.3899          568  29.4014                1.0834   
2019     280.6948          549  51.0018                1.1809   
2020     405.8264          504  49.0079                2.3683   
2021     341.8869          555  51.3514                1.5512   
2022     300.1892          804  36.1940                1.4897   
2023     226.9950          803  39.6015                0.9503   
2024     175.2896          380  47.6316                1.2058   
Overall 1859.2718    4163.0000  42.4934                1.4090   

        Avg Loss% per Trade Max Drawdown ROI/DD Ratio  
2018                -0.2871      -8.6793      14.7926  
2019                -0.2100      -4.1636      67.4169  
2020                -0.7025     -19.7286      20.5704  
2021                -0.3725     -11.3391      30.1512  
2022                -0.4883     -10.4254      28.7941  
2023                -0.2705     -13.3468      17.0075  
2024                -0.3230      -7.7494      22.6197  
Overall             -0.3888     -19.7286      94.2423

In [20]:
df.to_csv('Check Rolling Pivots TB v1.csv')